In [1]:
import sys
sys.path.append("/Users/rohan/public_html/Hegemon")
import StepMiner as smn
import HegemonUtil as hu
import re
import numpy as np
import scipy
import io
from scipy import io
import math
import itertools
from itertools import combinations 
import matplotlib.pyplot as plt
%matplotlib inline
from matplotlib.backends.backend_pdf import PdfPages
import pandas as pd
import statsmodels.stats.proportion
import seaborn as sns
import scanpy as sc
import GEOparse
import os

In [4]:
expr = pd.DataFrame(pd.read_csv("GSE175773-GPL23159-expr.txt", sep = '\t', header=0))
expr

ProbeID                                               Name  \
0      TC0100006437.hg.1  TC0100006437.hg.1:NM_001005484 // RefSeq // Ho...   
1      TC0100006476.hg.1  TC0100006476.hg.1:NM_152486 // RefSeq // Homo ...   
2      TC0100006479.hg.1  TC0100006479.hg.1:NM_198317 // RefSeq // Homo ...   
3      TC0100006480.hg.1  TC0100006480.hg.1:NM_001160184 // RefSeq // Ho...   
4      TC0100006483.hg.1  TC0100006483.hg.1:NM_005101 // RefSeq // Homo ...   
...                  ...                                                ...   
24346     ERCCmix2step44               23050127:--control->affx->ercc->step   
24347      ERCCmix2step6               23050128:--control->affx->ercc->step   
24348      ERCCmix2step7               23050129:--control->affx->ercc->step   
24349      ERCCmix2step8               23050130:--control->affx->ercc->step   
24350      ERCCmix2step9               23050131:--control->affx->ercc->step   

       GSM5346174  GSM5346175  GSM5346176  GSM5346177  GSM5346178  GSM5346179  \
0        2.848307    2.563595    2.258594    2.114720    2.499815    2.073724   
1        2.047301    1.976818    1.942180    1.924024    1.852075    2.003753   
2        2.430438    2.425430    2.304870    2.417169    2.364472    2.329256   
3        2.399609    2.479313    2.474563    2.324788    2.636372    2.456478   
4        2.698145    2.466162    2.635441    3.690886    2.592847    3.611066   
...           ...         ...         ...         ...         ...         ...   
24346    2.515816    2.372406    2.474109    2.370164    2.276654    2.448261   
24347    2.262713    2.645054    2.476693    2.514794    2.689230    2.580654   
24348    2.242651    2.372414    2.444998    2.318288    2.429078    2.385238   
24349    2.572305    2.626794    2.813313    2.596670    2.704485    2.522018   
24350    2.136145    2.281600    2.331828    2.145038    2.311227    2.273653   

       GSM5346180  GSM5346181  
0        2.237435    2.527145  
1        2.014866    2.053594  
2        2.346129    2.307525  
3        2.592876    2.624606  
4        2.573692    3.327026  
...           ...         ...  
24346    2.386621    2.461691  
24347    2.597400    2.546517  
24348    2.368830    2.427169  
24349    2.572230    2.759712  
24350    2.285935    2.228191  

[24351 rows x 10 columns]

In [22]:
# Fix gene names in expr file
names = [s[s.find('(')+1:s.find(')')] if "(" in s else s for s in expr["Name"]]
expr["Name"] = names
expr

ProbeID                                  Name  GSM5346174  \
0      TC0100006437.hg.1                                 OR4F5    2.848307   
1      TC0100006476.hg.1                                SAMD11    2.047301   
2      TC0100006479.hg.1                                KLHL17    2.430438   
3      TC0100006480.hg.1                               PLEKHN1    2.399609   
4      TC0100006483.hg.1                                 ISG15    2.698145   
...                  ...                                   ...         ...   
24346     ERCCmix2step44  23050127:--control->affx->ercc->step    2.515816   
24347      ERCCmix2step6  23050128:--control->affx->ercc->step    2.262713   
24348      ERCCmix2step7  23050129:--control->affx->ercc->step    2.242651   
24349      ERCCmix2step8  23050130:--control->affx->ercc->step    2.572305   
24350      ERCCmix2step9  23050131:--control->affx->ercc->step    2.136145   

       GSM5346175  GSM5346176  GSM5346177  GSM5346178  GSM5346179  GSM5346180  \
0        2.563595    2.258594    2.114720    2.499815    2.073724    2.237435   
1        1.976818    1.942180    1.924024    1.852075    2.003753    2.014866   
2        2.425430    2.304870    2.417169    2.364472    2.329256    2.346129   
3        2.479313    2.474563    2.324788    2.636372    2.456478    2.592876   
4        2.466162    2.635441    3.690886    2.592847    3.611066    2.573692   
...           ...         ...         ...         ...         ...         ...   
24346    2.372406    2.474109    2.370164    2.276654    2.448261    2.386621   
24347    2.645054    2.476693    2.514794    2.689230    2.580654    2.597400   
24348    2.372414    2.444998    2.318288    2.429078    2.385238    2.368830   
24349    2.626794    2.813313    2.596670    2.704485    2.522018    2.572230   
24350    2.281600    2.331828    2.145038    2.311227    2.273653    2.285935   

       GSM5346181  
0        2.527145  
1        2.053594  
2        2.307525  
3        2.624606  
4        3.327026  
...           ...  
24346    2.461691  
24347    2.546517  
24348    2.427169  
24349    2.759712  
24350    2.228191  

[24351 rows x 10 columns]

In [23]:
run ../moreprocessing.py

In [24]:
writeExprIdx(expr)

07-Jul-2022 11:56:00 DEBUG utils - Directory /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE175773 already exists. Skipping.
07-Jul-2022 11:56:00 INFO GEOparse - File already exist: using local version.
07-Jul-2022 11:56:00 INFO GEOparse - Parsing /mnt/booleanfs2/sahoo/Data/BooleanLab/Rohan/Data/Data/GSE175773/GSE175773_family.soft.gz: 
07-Jul-2022 11:56:00 DEBUG GEOparse - DATABASE: GeoMiame
07-Jul-2022 11:56:00 DEBUG GEOparse - SERIES: GSE175773
07-Jul-2022 11:56:00 DEBUG GEOparse - PLATFORM: GPL23159
07-Jul-2022 11:56:02 WARNING GEOTypes - Detected duplicated columns in d GPL23159. Correcting.

07-Jul-2022 11:56:02 DEBUG GEOparse - SAMPLE: GSM5346174
07-Jul-2022 11:56:02 DEBUG GEOparse - SAMPLE: GSM5346175
07-Jul-2022 11:56:02 DEBUG GEOparse - SAMPLE: GSM5346176
07-Jul-2022 11:56:02 DEBUG GEOparse - SAMPLE: GSM5346177
07-Jul-2022 11:56:02 DEBUG GEOparse - SAMPLE: GSM5346178
07-Jul-2022 11:56:02 DEBUG GEOparse - SAMPLE: GSM5346179
07-Jul-2022 11:56:02 DEBUG GEOparse - SAMPL

Starting expr
Done writing expr
Starting make_idx
Done with make_idx
